<font size="20">Final Map</font>

In [1]:
# The import command allows us to call on various libraries
import folium
import numpy as np
import pandas as pd
# import scipy.stats as stats
import geopandas as gpd
import matplotlib.pyplot as plt
import branca.colormap as cm
from geopy.geocoders import MapBox
from IPython.display import clear_output

# This allows us to create interactive plots with matplotlib
%matplotlib notebook

# You need this to query mapbox
api_key="pk.eyJ1IjoianVuZXNwYWNlYm9vdHMiLCJhIjoiY2twY3g4aXloMWFlcDJzbXN3aG95aG5uZiJ9.mFiJt0MIfL1MiJ2rB2xhKQ"

if api_key == "":
    print('Please enter your API key to continue!')
else:
    print('Packages Loaded')

Packages Loaded


# Importing Census Data


In [3]:
# the .read_file() function reads shapefiles
MVan_CT = gpd.read_file('Data/CensusTracts/SimplyAnalytics_Shapefiles_2021-06-01_17_44_45_9e5629a2de473cd5362919f9edc33853.shp')
print(MVan_CT.crs)
MVan_CT = MVan_CT.rename(columns={
'VALUE0': 'Aboriginal identity, 2016',
'VALUE1': 'Population, 2016',
'VALUE2': 'Total visible minority population, 2016'
                    })

MVan_CT['NonWhitePCT'] = MVan_CT[['Aboriginal identity, 2016',
'Total visible minority population, 2016']].sum(axis=1)/MVan_CT['Population, 2016']*100

# .to_crs()changes the coordinate system
# Provincial_Data = Provincial_Data.to_crs('EPSG:4326')
# .to_file() saves our data to the specified format
print('Data Converted')
print(MVan_CT.NonWhitePCT.describe())
MVan_CT.to_file("Data/MVan_CT.json", driver = "GeoJSON")
MVan_CT.head()

epsg:4326
Data Converted
count    474.000000
mean      50.244791
std       23.706768
min        4.712042
25%       28.461442
50%       49.974349
75%       70.736891
max      100.000000
Name: NonWhitePCT, dtype: float64


spatial_id                      name  Aboriginal identity, 2016  \
0  9330001.01  CT0001.01, Vancouver, BC                      175.0   
1  9330001.02  CT0001.02, Vancouver, BC                       74.0   
2  9330002.01  CT0002.01, Vancouver, BC                       95.0   
3  9330002.03  CT0002.03, Vancouver, BC                       65.0   
4  9330002.04  CT0002.04, Vancouver, BC                       44.0   

   Population, 2016  Total visible minority population, 2016  \
0            6293.0                                   3129.0   
1            5456.0                                   3633.0   
2            6150.0                                   4027.0   
3            4077.0                                   3547.0   
4            4509.0                                   2764.0   

                                            geometry  NonWhitePCT  
0  POLYGON ((-123.02367 49.21204, -123.02371 49.2...    52.502781  
1  POLYGON ((-123.02768 49.21005, -123.02807 49.2...    67.943548  
2  POLYGON ((-123.04137 49.21830, -123.04138 49.2...    67.024390  
3  POLYGON ((-123.05938 49.21195, -123.05917 49.2...    88.594555  
4  POLYGON ((-123.05970 49.21147, -123.05917 49.2...    62.275449

# Importing Police Involved Deaths Data


In [43]:
PID_BC = pd.read_csv('Data/BC_Data.csv',index_col='id_victim',parse_dates=['date'])
# print(PID.columns)
PID_BC['postal_code'] = PID_BC['postal_code'].fillna('')
# PID_BC['postal_code'] = PID_BC['postal_code'].fillna('')
# PID_BC = PID.loc[((PID['prov']=='BC')&(PID['postal_code']!='Unspecified'))].copy()
print(PID_BC['postal_code'].count())
# print(PID_BC['city_town'].unique())
PID_BC['city_town'] = PID_BC['city_town'].str.split(';').str[0]
# PID_BC['city_town']
# We'll create empty columns for latitude & longitude
# We'll create a "notes" column as well
PID_BC['address_intersection']=PID_BC['address_intersection'].fillna('')
PID_BC['race']=PID_BC['race'].fillna('Unspecified')
PID_BC['gender']=PID_BC['gender'].fillna('Unspecified')
PID_BC['latitude'] = np.nan
PID_BC['longitude'] = np.nan
PID_BC['geocoding_Notes'] = ''
print(PID_BC.columns)
print(PID_BC.loc[PID_BC.index=='MR_134','city_town'])

120
Index(['date', 'date.1', 'first_name', 'last_name', 'middle_name',
       'alias_nickname', 'age', 'gender', 'race', 'prov', 'department',
       'cause_death', 'DEATH CATEGORY', 'data_source', 'Link', 'summary',
       'name', 'KCC_ID', 'ds_rank', 'index', 'id_incident', 'day_week',
       'city_town', 'address_intersection', 'postal_code', 'location_type',
       'ethnic_ancestry', 'immigrant_refugee_naturalized', 'armed_type',
       'taser_deployed', 'injured_officer', 'excited_delirium',
       'mentral_distress_disorder', 'substance_abuse', 'charge_type',
       'charges', 'officers involved', 'Check', 'Inquest date', 'extra_source',
       'latitude', 'longitude', 'geocoding_Notes'],
      dtype='object')
id_victim
MR_134    Vancouver
Name: city_town, dtype: object


# Geocoding

In [47]:
geolocator = MapBox(api_key=api_key)

i = 0
for index, row in PID_BC.iterrows():
    attempt = ' '.join([row['address_intersection'], row['city_town'], row['prov'], row['postal_code'],'Canada'])
#     print(i)
#     if i == 'MR_134':
#         print('Skpped?')
    try:
#         Progress report
#         if i % 25 == 0:
#             clear_output()
#             print("PROGRESS: {} out of {}. Currently at: {}".format(i, len(PID_BC), i))

        g = geolocator.geocode(attempt,timeout=3)
#         print(row['city_town'] not in g)
#         if index == 'MR_134':
        print(attempt)
        print(g)
        print()
        PID_BC.loc[PID_BC.index==index,
                    ['latitude','longitude']]=g.latitude,g.longitude
    except:
        
        Police_Killings.loc[Police_Killings['postal_code']==row['postal_code'],
                    'geocoding_Notes']='Geocoding Failed'
        pass
    i += 1
print('Geocoding Done')


Highway 1 Bruhn Bridge Sicamous BC V0E 2V0 Canada
V0E 2V0, Sicamous, British Columbia, Canada

17000 21 Avenue Surrey BC V3S 9Z4 Canada
17000 21 Avenue, Surrey, British Columbia V3Z 9Z4, Canada

501 Powell St Vancouver BC V6A 1G8 Canada
501 Powell Street, Vancouver, British Columbia V6A 1G8, Canada

 Opitsaht BC  Canada
British Columbia, Canada

Princess Avenue and Hastings Street Vancouver BC V6A 1P9 Canada
Princess Avenue, Vancouver, British Columbia V6A 3C9, Canada

306 Terminal Ave Vancouver BC V6A 3W9 Canada
306 Terminal Avenue, Vancouver, British Columbia V6A 3W9, Canada

600 Douglas Street Victoria BC V8V 2P8 Canada
600 Douglas Street, Victoria, British Columbia V8V 2P8, Canada

4300-block of Munrose Street Gitlaxt'aamiks BC V0J 1A0 Canada
V0J 1A0, Nisga'A, British Columbia, Canada

Fleetwood Surrey BC V3R 3P3 Canada
Fleetwood Drive, Surrey, British Columbia V3R 1B5, Canada

4216 Wilkinson Rd Victoria BC V8Z 5B2 Canada
4216 Wilkinson Road, Saanich, British Columbia V8Z 5B2, Cana

320 East Hastings Street Vancouver BC V6A 1P4 Canada
320 East Hastings Street, Vancouver, British Columbia V6A 1P4, Canada

6116 14th Ave. Burnaby BC V3N 1Y5 Canada
6116 14th Avenue, Burnaby, British Columbia V3N 1Y5, Canada

 Surrey BC  Canada
Surrey, British Columbia, Canada

3351 BC-16 Smithers BC V0J 2N0 Canada
V0J 2N0, Smithers, British Columbia, Canada

9743 Oak St. Chilliwack BC V2P 5A3 Canada
9743 Oak Street, Chilliwack, British Columbia V2P 5A3, Canada

Kinnaird Bridge, Highway 3 Castlegar BC V1N 3W5 Canada
V1N 3W5, Castlegar, British Columbia, Canada

2250 Trans-Canada Hwy Kamloops BC V2E 2T1 Canada
2250 Trans-Canada Highway, Kamloops, British Columbia V2E 2T1, Canada

10355 King George Highway Surrey BC V3T 2W6 Canada
10355 King George Boulevard, Surrey, British Columbia V3T 2W6, Canada

33056 Mill Lake Rd Abbotsford BC V2S 2A3 Canada
33056 Mill Lake Road, Abbotsford, British Columbia V2S 2A3, Canada

3400 W 33rd Ave Vancouver BC V6N 2H2 Canada
3400 West 33rd Avenue, Vancouv

In [48]:
Failures = (PID_BC.loc[PID_BC['geocoding_Notes']=='Geocoding Failed',
                          ['prov','postal_code']])
print(Failures)

# print()\
PID_BC.to_csv('BC_Geocoded.csv')

Empty DataFrame
Columns: [prov, postal_code]
Index: []


In [6]:
# "def" defines our function "plot_point()", which takes five "arguments":
    # Map: The map you're working with
    # X & Y: lattitude & longitude
    # Popup_Text: What do we want the popup to say?
    # Color: We'll set a defualt, but we can override with what colour do we want
        # Everything else will remain the same for every point, so we can set them as default values
    # Defaults can be over written by assigning them anoter value
def plot_point(Map,X,Y,Popup_Text,Color='olive',Radius=5,Opacity=.75,LineColor='black',LineWidth=.15):
    folium.CircleMarker(
        # The coordiatnates
        location=[X,Y],
        # Text description
        popup=Popup_Text,
        # sets the fill color for the point
        fill_color=Color,
        # Size of the marker
        radius=Radius,
        # Opacity of the circle
        fill_opacity = Opacity,
        # Sets the line color for the edge
        color=LineColor,
        # Width of the border line
        line_weight=LineWidth,
    ).add_to(Map)

# Make a webmap showing all incidents in BC & census data for metro vancouver

In [7]:

BC_Map = folium.Map(
    location=['49.260438','-123.088896'],
    zoom_start=11,
    tiles='Stamen Toner'
)


# The .features.Chloropleth() function allows us to classify our data
# We give function the location of our GeoJSON file

folium.features.Choropleth('Data/MVan_CT.json',
                           # It will match the geometry data up with a pandas or geopandas dataframe
                            data=MVan_CT,
                            columns=['spatial_id','NonWhitePCT'],
                           # They key in the GeoJSON file to match by
                            key_on='feature.properties.spatial_id',
                           # If we define bins, it will split where we tell it to
                            bins = [0,25,50,75,101],
                            fill_color='PuRd',
                            fill_opacity = 1,
                            smooth=2,
                           # The layer name
                            name='Non-White Population %',
                           # The legend label
                            legend_name='Non-White',
                           # Whether it shows up by default or must be turned on with the legend
                            show=False
                          ).add_to(BC_Map)


colormap = cm.linear.PuRd_05.scale(MVan_CT['Population, 2016'].min(), MVan_CT['Population, 2016'].max())
colormap = cm.LinearColormap(['white','blue'])
colormap = colormap.to_step(index=[MVan_CT['Population, 2016'].min(),
                                   MVan_CT['Population, 2016'].quantile(.25),
                                   MVan_CT['Population, 2016'].quantile(.5), 
                                   MVan_CT['Population, 2016'].quantile(.75), 
                                   MVan_CT['Population, 2016'].max()],
                           round_method =None)
colormap.caption = 'Total Population %'
# colormap.caption = 'Police Killings/ Year / Million People (2000-2017)'
colormap.add_to(BC_Map)

folium.GeoJson(
    'Data/MVan_CT.json',
    name='Total Population',
    smooth_factor=1.75,
    style_function = lambda x:{'color':'black',
                               "weight": 1,
                               "fillOpacity": 1,
                              'fillColor':colormap(x['properties']['Population, 2016'])
                              },
    tooltip=folium.features.GeoJsonTooltip(fields=['Aboriginal identity, 2016',
    'Total visible minority population, 2016',
    'NonWhitePCT'],
       aliases=['Indigineous Population',
                'Visible Minorit (non-Indigenou) Poulation','NonWhitePCT']
                                          ),
    show = True
).add_to(BC_Map)



group = folium.FeatureGroup(name='Deaths')
for index, row in PID_BC.iterrows():
    # if the geocoding didn't fail, we'll plot the point, colored by the province
    if row['geocoding_Notes'] != 'Geocoding Failed':
#         print(row['race'], row['gender'],str(row['age']))
        plot_point(Map=group,
                   X=row['latitude'],
                   Y=row['longitude'],
                   Popup_Text=row['race']+' '+ row['gender'] + ' '+ str(row['age'])\
                     + ' '+ row['city_town'] + ' '+ row['prov']+ ' '+ row['postal_code'],
                   Color='red'#color_Scheme[row['prov']]
                  )

group.add_to(BC_Map)

folium.LayerControl().add_to(BC_Map)
BC_Map

In [ ]:
BC_Map.save('PoliceViolenceIncidents_BC.html')
print('Map Saved!')